In [1]:
import xarray as xr
import hvplot.xarray
import hvplot.pandas
import matplotlib
import numpy as np
import cartopy
from dask.distributed import Client
import fsspec

In [2]:
CLIENT_KWARGS = {'endpoint_url': 'https://s3.wasabisys.com',
                 'region_name': 'us-east-1'}
CONFIG_KWARGS = {'max_pool_connections': 100}
STORAGE_OPTIONS = {'anon': True,
                   'client_kwargs': CLIENT_KWARGS,
                   'config_kwargs': CONFIG_KWARGS
                   }

fs = fsspec.filesystem('s3', **STORAGE_OPTIONS)

In [3]:
client = Client()
client

<Client: 'tcp://127.0.0.1:44981' processes=8 threads=32, memory=135.00 GB>

In [4]:
mapper = fs.get_mapper('s3://scdna/zarr/version/1.1')
ds = xr.open_zarr(mapper, consolidated=True)
ds

<xarray.Dataset>
Dimensions:    (ID: 27276, time: 14610)
Coordinates:
  * ID         (ID) <U13 'GS91066022701' 'GHMQW00022701' ... 'ECCA008402568'
    elevation  (ID) float32 dask.array<chunksize=(1000,), meta=np.ndarray>
    latitude   (ID) float32 dask.array<chunksize=(1000,), meta=np.ndarray>
    longitude  (ID) float32 dask.array<chunksize=(1000,), meta=np.ndarray>
  * time       (time) datetime64[ns] 1979-01-01 1979-01-02 ... 2018-12-31
Data variables:
    prcp       (ID, time) float32 dask.array<chunksize=(1000, 1000), meta=np.ndarray>
    prcp_flag  (ID, time) float64 dask.array<chunksize=(1000, 1000), meta=np.ndarray>
    prcp_kge   (ID) float32 dask.array<chunksize=(1000,), meta=np.ndarray>
    sflag      (ID) <U3 dask.array<chunksize=(1000,), meta=np.ndarray>
    tmax       (ID, time) float32 dask.array<chunksize=(1000, 1000), meta=np.ndarray>
    tmax_flag  (ID, time) float64 dask.array<chunksize=(1000, 1000), meta=np.ndarray>
    tmax_kge   (ID) float32 dask.array<chunksize=(1000,), meta=np.ndarray>
    tmin       (ID, time) float32 dask.array<chunksize=(1000, 1000), meta=np.ndarray>
    tmin_flag  (ID, time) float64 dask.array<chunksize=(1000, 1000), meta=np.ndarray>
    tmin_kge   (ID) float32 dask.array<chunksize=(1000,), meta=np.ndarray>

In [5]:
%%time
ds \
.ID \
.to_dataframe() \
.hvplot \
.points('longitude', 'latitude', 
        geo=True, 
        color='elevation', 
        alpha=0.2,
        xlim=(-180, -30), 
        ylim=(0, 72),
        cmap='terrain',
        width=700,
        height=450,
        tiles='EsriTerrain',
        hover_cols=['elevation'],
        title=f'Elevation point from {ds.ID.size} stations in the SCDNA v1.1 dataset')

CPU times: user 10.5 s, sys: 2.29 s, total: 12.8 s
Wall time: 13.5 s


:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [longitude,latitude]   (elevation)

In [6]:
%%time
time = '1996-07-19'

ds.prcp\
.sel(time=time) \
.to_dataframe() \
.replace({0:np.nan}) \
.dropna(how='any') \
.hvplot \
.points('longitude', 'latitude',
        geo=True, 
        color='prcp',
        alpha=0.5,
        xlim=(-180, -30), 
        ylim=(0, 72),
        width=700,
        cmap='gist_ncar',
        clim=(0,100),
        height=450,
        hover_cols=['ID','prcp'],
        tiles='ESRI',
        title='Daily precipitation during the peak of the Saguenay flood')

CPU times: user 721 ms, sys: 55.5 ms, total: 777 ms
Wall time: 4.71 s


:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [longitude,latitude]   (prcp,ID)

In [7]:
%%time

bndbox = [47, 49, -72, -70] # Sud, Nord, Est, Ouest

ds.where((ds.latitude > bndbox[0]) &
         (ds.latitude < bndbox[1]) &
         (ds.longitude > bndbox[2]) &
         (ds.longitude < bndbox[3]), 
          drop=True) \
.prcp \
.drop(['elevation', 'longitude','latitude'])\
.sel(time=ds.time.dt.year.isin([1996])) \
.hvplot(x='time',
        y='prcp',
        by='ID',
        kind='scatter',
        grid=True,
        width=900,
        height=450,
        hover_cols=['ID','prcp'],
        title='Precipitation time-series for available stations in the Saguenay region in 1996' )

CPU times: user 531 ms, sys: 53.9 ms, total: 585 ms
Wall time: 3.72 s


:NdOverlay   [ID]
   :Scatter   [time]   (prcp,ID)

In [11]:
%%time

ds.where((ds.latitude > bndbox[0]) &
         (ds.latitude < bndbox[1]) &
         (ds.longitude > bndbox[2]) &
         (ds.longitude < bndbox[3]),
          drop=True) \
.prcp \
.drop(['elevation', 'longitude','latitude'])\
.sel(time=ds.time.dt.year.isin([1996])) \
.dropna(dim='ID') \
.max('time') \
.to_dataframe() \
.hvplot \
.bar(grid=True, 
     rot=45,
     height=400,
     color='prcp',
     title='Precipitation annual maxima for available stations in the Saguenay region in 1996')

CPU times: user 618 ms, sys: 46.6 ms, total: 664 ms
Wall time: 3.6 s


:Bars   [ID]   (prcp)

In [9]:
%%time

ds.where((ds.latitude > bndbox[0]) &
         (ds.latitude < bndbox[1]) &
         (ds.longitude > bndbox[2]) &
         (ds.longitude < bndbox[3]),
          drop=True) \
.prcp \
.drop(['elevation'])\
.sel(time=ds.time.dt.year.isin([1996])) \
.dropna(dim='ID') \
.rolling(time=3) \
.sum() \
.max('time') \
.to_dataframe() \
.hvplot \
.points('longitude', 'latitude',
        geo=True, 
        color='prcp',
        alpha=1,
        width=700,
        cmap='rainbow',
        height=450,
        hover_cols=['ID','prcp'],
        tiles='EsriReference',
        title='72h precipitation annual maxima in the Saguenay region in 1996',
        s=200)

CPU times: user 698 ms, sys: 49.8 ms, total: 748 ms
Wall time: 3.71 s


:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [longitude,latitude]   (prcp,ID)

In [10]:
%%time

dst = ds.where((ds.latitude > bndbox[0]) &
         (ds.latitude < bndbox[1]) &
         (ds.longitude > bndbox[2]) &
         (ds.longitude < bndbox[3]),
          drop=True) \
[['tmax','tmin', 'prcp']] \
.drop(['elevation'])\
.dropna(dim='ID') \
.drop(['latitude','longitude'])

(dst.prcp.mean('ID').hvplot.scatter(grid=True, 
                                    label='prcp',
                                    color='prcp',
                                    title=f'Average precipitation over {dst.ID.size} stations in the Saguenay region') + \
(dst.tmax.mean('ID').hvplot(grid=True, 
                           label='tmax',
                           title=f'Average tmax and tmin over {dst.ID.size} stations in the Saguenay region')* \
dst.tmin.mean('ID').hvplot(grid=True, 
                           label='tmin'))).cols(1)

CPU times: user 2.48 s, sys: 281 ms, total: 2.76 s
Wall time: 17.8 s


:Layout
   .Scatter.Prcp :Scatter   [time]   (prcp)
   .Overlay.I    :Overlay
      .Curve.Tmax :Curve   [time]   (tmax)
      .Curve.Tmin :Curve   [time]   (tmin)